In [1]:
import json
import requests
from decimal import Decimal
import logging
import re  # Import regular expressions
import io
from rich import print as rprint
import pandas as pd
import pprint

genesis_url = 'https://www-genesis.destatis.de/genesisWS/rest/2020/data/cube?'
user_id = 'DE17T29R57'
password = '4Bf/3Ap)3]r2,,h'

In [17]:
# Wärmepreisindex
cubecode = '61111BM006'
areatype = 'all'
category = 'all'
content = ''
start_year = ''
classifier1 = 'CC13B1'
key1 = 'CC13-77'
lang = 'en'

# Destatis Base Url
url = (f"{genesis_url}username={user_id}&password={password}&language=de&name={cubecode}&area={areatype}"
       f"&compress=true&contents={content}&startyear={start_year}")

# Add Classifyers to url
if classifier1:
       url += f'&classifyingvariable1={classifier1}'    
if key1:
       url += f'&classifyingkey1={key1}'

# request 
response = requests.get(url)
# First, parse the JSON response with Decimal conversion for floats
#Float types are not supported with dynamodb; use Decimal types instead
parsed_json = json.loads(response.text, parse_float=Decimal)

# Now, access the 'Content' part and split it by newline
data = parsed_json["Object"]['Content'].split('\n')


# Compile a regex pattern to find sequences of digits ending with "=100"
info_pattern = re.compile(r'\d+=100')

# Extract only the parts of lines that match the pattern "*=100"
info_matches = []
for line in data:
    matches = info_pattern.findall(line)  # find all matches in a line
    info_matches.extend(matches)  # add found matches to the list

# Convert info_matches to a single string to append to each filtered line
info_matches_str = ', '.join(info_matches)

# Compile a regex pattern to find sequences of digits ending with "=100"
info_pattern = re.compile(r'\d+=100')

# Extract only the parts of lines that match the pattern "*=100"
info_matches = []
for line in data:
    matches = info_pattern.findall(line)  # find all matches in a line
    info_matches.extend(matches)  # add found matches to the list

# Convert info_matches to a single string to append to each filtered line
info_matches_str = ', '.join(info_matches)

# Filter out the relevant lines and append the matches string to each
filtered_response = [line + " " + info_matches_str for line in data if 'D' in line and 'e' in line and ('MONAT' in line or 'QUART' in line)]

# Split each line into its components and extract the relevant information
data = [{'field_D': parts[0],
         'field_DG': parts[1],
         'classifyingkey1': parts[2],
         'period': parts[3],
         'year': int(parts[4]),
         'value': float(parts[5]),
         'field_e': parts[6],
         'base': info_matches_str
        }
        for parts in (line.split(';') for line in filtered_response)]

# Create a DataFrame from the extracted data
df = pd.DataFrame(data)

# Determine if the data is monthly or quarterly based on the unique values in the 'period' column
if df['period'].str.contains('Q').any():
    period_key = 'quarter'
else:
    period_key = 'month'

# Create result dict
result = {'cubeCode': cubecode, 'content': content, 'classifyingVar1': classifier1, 'classifyingKey1': key1, 'data': []}
for year, group in df.groupby('year'):
    year_data = {
        'year': year,
        'df': [{
            period_key: row['period'],
            'value': row['value'],
            'base': row['base']
            } for _, row in group.iterrows()]
    }
    result['data'].append(year_data)
    
j = json.dumps(result, indent=4)
rprint(j)

{
    "cubeCode": "61111BM006",
    "content": "",
    "classifyingVar1": "CC13B1",
    "classifyingKey1": "CC13-77",
    "data": [
        {
            "year": 1991,
            "df": [
                {
                    "month": "MONAT01",
                    "value": 38.7,
                    "base": "2020=100"
                },
                {
                    "month": "MONAT02",
                    "value": 38.9,
                    "base": "2020=100"
                },
                {
                    "month": "MONAT03",
                    "value": 39.6,
                    "base": "2020=100"
                },
                {
                    "month": "MONAT04",
                    "value": 39.8,
                    "base": "2020=100"
                },
                {
                    "month": "MONAT05",
                    "value": 40.0,
                    "base": "2020=100"
                },
                {
                    "month": "MONAT06",
                    "value": 40.3,
                    "base": "2020=100"
                },
                {
                    "month": "MONAT07",
                    "value": 40.6,
                    "base": "2020=100"
                },
                {
                    "month": "MONAT08",
                    "value": 40.6,
                    "base": "2020=100"
                },
                {
                    "month": "MONAT09",
                    "value": 41.0,
                    "base": "2020=100"
                },
                {
                    "month": "MONAT10",
                    "value": 53.0,
                    "base": "2020=100"
                },
                {
                    "month": "MONAT11",
                    "value": 52.7,
                    "base": "2020=100"
                },
                {
                    "month": "MONAT12",
                    "value": 52.7,
                    "base": "2020=100"
                }
            ]
        },
        {
            "year": 1992,
            "df": [
                {
                    "month": "MONAT01",
                    "value": 52.6,
                    "base": "2020=100"
                },
                {
                    "month": "MONAT02",
                    "value": 52.4,
                    "base": "2020=100"
                },
                {
                    "month": "MONAT03",
                    "value": 51.9,
                    "base": "2020=100"
                },
                {
                    "month": "MONAT04",
                    "value": 52.0,
                    "base": "2020=100"
                },
                {
                    "month": "MONAT05",
                    "value": 52.0,
                    "base": "2020=100"
                },
                {
                    "month": "MONAT06",
                    "value": 52.2,
                    "base": "2020=100"
                },
                {
                    "month": "MONAT07",
                    "value": 52.4,
                    "base": "2020=100"
                },
                {
                    "month": "MONAT08",
                    "value": 52.4,
                    "base": "2020=100"
                },
                {
                    "month": "MONAT09",
                    "value": 52.4,
                    "base": "2020=100"
                },
                {
                    "month": "MONAT10",
                    "value": 52.0,
                    "base": "2020=100"
                },
                {
                    "month": "MONAT11",
                    "value": 51.8,
                    "base": "2020=100"
                },
                {
                    "month": "MONAT12",
                    "value": 51.8,
                    "base": "2020=100"
                }
            ]
        },
        {
            "year": 1993,
            "df": [
                {
          

In [18]:
# Dieselkraftstoff ab Tankstelle
cubecode = '61241BM007'
areatype = 'all'
content = ''
start_year = ''
classifier1 = 'GP19N1'
key1 = 'GP19-1920260053'
lang = 'en'

# Destatis Base Url
url = (f"{genesis_url}username={user_id}&password={password}&language=de&name={cubecode}&area={areatype}"
       f"&compress=true&contents={content}&startyear={start_year}")

# Add Classifyers to url
if classifier1:
       url += f'&classifyingvariable1={classifier1}'    
if key1:
       url += f'&classifyingkey1={key1}'

# request 
response = requests.get(url)
data = json.loads(response.text)["Object"]['Content'].split('\n')

# Compile a regex pattern to find sequences of digits ending with "=100"
info_pattern = re.compile(r'\d+=100')

# Extract only the parts of lines that match the pattern "*=100"
info_matches = []
for line in data:
    matches = info_pattern.findall(line)  # find all matches in a line
    info_matches.extend(matches)  # add found matches to the list

# Convert info_matches to a single string to append to each filtered line
info_matches_str = ', '.join(info_matches)

# Compile a regex pattern to find sequences of digits ending with "=100"
info_pattern = re.compile(r'\d+=100')

# Extract only the parts of lines that match the pattern "*=100"
info_matches = []
for line in data:
    matches = info_pattern.findall(line)  # find all matches in a line
    info_matches.extend(matches)  # add found matches to the list

# Convert info_matches to a single string to append to each filtered line
info_matches_str = ', '.join(info_matches)

# Filter out the relevant lines and append the matches string to each
filtered_response = [line + " " + info_matches_str for line in data if 'D' in line and 'e' in line and ('MONAT' in line or 'QUART' in line)]

# Split each line into its components and extract the relevant information

data = [{'field_D': parts[0],
         'field_DG': parts[1],
         'classifyingkey1': parts[2],
         'period': parts[3],
         'year': int(parts[4]),
         'value': float(parts[5]),
         'field_e': parts[6],
         'base': info_matches_str
        }
        for parts in (line.split(';') for line in filtered_response)]

# Create a DataFrame from the extracted data
df = pd.DataFrame(data)

# Determine if the data is monthly or quarterly based on the unique values in the 'period' column
if df['period'].str.contains('Q').any():
    period_key = 'quarter'
else:
    period_key = 'month'

# Create result dict
result = {'cubeCode': cubecode, 'content': content, 'classifyingVar1': classifier1, 'classifyingKey1': key1, 'data': []}
for year, group in df.groupby('year'):
    year_data = {
        'year': year,
        'df': [{
            period_key: row['period'],
            'value': row['value'],
            'base': row['base']
            } for _, row in group.iterrows()]
    }
    result['data'].append(year_data)
    
j = json.dumps(result, indent=4)
rprint(j)

{
    "cubeCode": "61241BM007",
    "content": "",
    "classifyingVar1": "GP19N1",
    "classifyingKey1": "GP19-1920260053",
    "data": [
        {
            "year": 2000,
            "df": [
                {
                    "month": "MONAT01",
                    "value": 55.4,
                    "base": "2021=100"
                },
                {
                    "month": "MONAT02",
                    "value": 57.1,
                    "base": "2021=100"
                },
                {
                    "month": "MONAT03",
                    "value": 56.5,
                    "base": "2021=100"
                },
                {
                    "month": "MONAT04",
                    "value": 52.0,
                    "base": "2021=100"
                },
                {
                    "month": "MONAT05",
                    "value": 52.5,
                    "base": "2021=100"
                },
                {
                    "month": "MONAT06",
                    "value": 55.4,
                    "base": "2021=100"
                },
                {
                    "month": "MONAT07",
                    "value": 54.8,
                    "base": "2021=100"
                },
                {
                    "month": "MONAT08",
                    "value": 56.4,
                    "base": "2021=100"
                },
                {
                    "month": "MONAT09",
                    "value": 63.4,
                    "base": "2021=100"
                },
                {
                    "month": "MONAT10",
                    "value": 61.7,
                    "base": "2021=100"
                },
                {
                    "month": "MONAT11",
                    "value": 62.9,
                    "base": "2021=100"
                },
                {
                    "month": "MONAT12",
                    "value": 61.7,
                    "base": "2021=100"
                }
            ]
        },
        {
            "year": 2001,
            "df": [
                {
                    "month": "MONAT01",
                    "value": 59.0,
                    "base": "2021=100"
                },
                {
                    "month": "MONAT02",
                    "value": 59.5,
                    "base": "2021=100"
                },
                {
                    "month": "MONAT03",
                    "value": 59.4,
                    "base": "2021=100"
                },
                {
                    "month": "MONAT04",
                    "value": 59.6,
                    "base": "2021=100"
                },
                {
                    "month": "MONAT05",
                    "value": 60.1,
                    "base": "2021=100"
                },
                {
                    "month": "MONAT06",
                    "value": 59.7,
                    "base": "2021=100"
                },
                {
                    "month": "MONAT07",
                    "value": 59.2,
                    "base": "2021=100"
                },
                {
                    "month": "MONAT08",
                    "value": 58.3,
                    "base": "2021=100"
                },
                {
                    "month": "MONAT09",
                    "value": 58.6,
                    "base": "2021=100"
                },
                {
                    "month": "MONAT10",
                    "value": 57.2,
                    "base": "2021=100"
                },
                {
                    "month": "MONAT11",
                    "value": 56.5,
                    "base": "2021=100"
                },
                {
                    "month": "MONAT12",
                    "value": 55.9,
                    "base": "2021=100"
                }
            ]
        },
        {
            "year": 2002,
            "df": [
                {
  

In [20]:
# Dampfkessel (Dampferzeuger) (ohne Zentralheizungs- kessel); Kernreaktoren, Teile dafür
cubecode = '61241BM003'
areatype = 'all'
content = ''
start_year = ''
classifier1 = 'GP19M3'
key1 = 'GP19-253'
lang = 'en'

# Destatis Base Url
url = (f"{genesis_url}username={user_id}&password={password}&language=de&name={cubecode}&area={areatype}"
       f"&compress=true&contents={content}&startyear={start_year}")

# Add Classifyers to url
if classifier1:
       url += f'&classifyingvariable1={classifier1}'
if key1:
       url += f'&classifyingkey1={key1}'

# request
response = requests.get(url)
data = json.loads(response.text)["Object"]['Content'].split('\n')

# Compile a regex pattern to find sequences of digits ending with "=100"
info_pattern = re.compile(r'\d+=100')

# Extract only the parts of lines that match the pattern "*=100"
info_matches = []
for line in data:
    matches = info_pattern.findall(line)  # find all matches in a line
    info_matches.extend(matches)  # add found matches to the list

# Convert info_matches to a single string to append to each filtered line
info_matches_str = ', '.join(info_matches)

# Filter out the relevant lines and append the matches string to each
filtered_response = [line + " " + info_matches_str for line in data if 'D' in line and 'e' in line and ('MONAT' in line or 'QUART' in line)]

#rprint(filtered_response)
# Split each line into its components and extract the relevant information

data = [{'field_D': parts[0],
         'classifyingkey1': parts[1],
         'field_DG': parts[2],
         'period': parts[3],
         'year': int(parts[4]),
         'value': float(parts[5]),
         'field_e': parts[6],
         'base': info_matches_str
        }
        for parts in (line.split(';') for line in filtered_response)]

# Create a DataFrame from the extracted data
df = pd.DataFrame(data)

# Determine if the data is monthly or quarterly based on the unique values in the 'period' column
if df['period'].str.contains('Q').any():
    period_key = 'quarter'
else:
    period_key = 'month'

# Create result dict
result = {'cubeCode': cubecode, 'content': content, 'classifyingVar1': classifier1, 'classifyingKey1': key1, 'data': []}
for year, group in df.groupby('year'):
    year_data = {
        'year': year,
        'df': [{
            period_key: row['period'],
            'value': row['value'],
            'base': row['base']
            } for _, row in group.iterrows()]
    }
    result['data'].append(year_data)

j = json.dumps(result, indent=4)
rprint(j)

{
    "cubeCode": "61241BM003",
    "content": "",
    "classifyingVar1": "GP19M3",
    "classifyingKey1": "GP19-253",
    "data": [
        {
            "year": 1976,
            "df": [
                {
                    "month": "MONAT01",
                    "value": 22.3,
                    "base": "2021=100"
                },
                {
                    "month": "MONAT02",
                    "value": 22.3,
                    "base": "2021=100"
                },
                {
                    "month": "MONAT03",
                    "value": 22.3,
                    "base": "2021=100"
                },
                {
                    "month": "MONAT04",
                    "value": 23.4,
                    "base": "2021=100"
                },
                {
                    "month": "MONAT05",
                    "value": 23.4,
                    "base": "2021=100"
                },
                {
                    "month": "MONAT06",
                    "value": 23.4,
                    "base": "2021=100"
                },
                {
                    "month": "MONAT07",
                    "value": 23.6,
                    "base": "2021=100"
                },
                {
                    "month": "MONAT08",
                    "value": 23.6,
                    "base": "2021=100"
                },
                {
                    "month": "MONAT09",
                    "value": 23.6,
                    "base": "2021=100"
                },
                {
                    "month": "MONAT10",
                    "value": 23.6,
                    "base": "2021=100"
                },
                {
                    "month": "MONAT11",
                    "value": 23.6,
                    "base": "2021=100"
                },
                {
                    "month": "MONAT12",
                    "value": 23.6,
                    "base": "2021=100"
                }
            ]
        },
        {
            "year": 1977,
            "df": [
                {
                    "month": "MONAT01",
                    "value": 24.6,
                    "base": "2021=100"
                },
                {
                    "month": "MONAT02",
                    "value": 24.7,
                    "base": "2021=100"
                },
                {
                    "month": "MONAT03",
                    "value": 24.7,
                    "base": "2021=100"
                },
                {
                    "month": "MONAT04",
                    "value": 25.3,
                    "base": "2021=100"
                },
                {
                    "month": "MONAT05",
                    "value": 25.3,
                    "base": "2021=100"
                },
                {
                    "month": "MONAT06",
                    "value": 25.3,
                    "base": "2021=100"
                },
                {
                    "month": "MONAT07",
                    "value": 25.3,
                    "base": "2021=100"
                },
                {
                    "month": "MONAT08",
                    "value": 25.3,
                    "base": "2021=100"
                },
                {
                    "month": "MONAT09",
                    "value": 25.3,
                    "base": "2021=100"
                },
                {
                    "month": "MONAT10",
                    "value": 25.3,
                    "base": "2021=100"
                },
                {
                    "month": "MONAT11",
                    "value": 25.3,
                    "base": "2021=100"
                },
                {
                    "month": "MONAT12",
                    "value": 25.3,
                    "base": "2021=100"
                }
            ]
        },
        {
            "year": 1978,
            "df": [
                {
         

In [21]:
# Elektr. Strom, bei Abgabe an gewerbliche Anlagen
cubecode = '61241BM006'
areatype = 'all'
content = ''
start_year = ''
classifier1 = 'GP19M6'
key1 = 'GP19-351113'
lang = 'en'

# Destatis Base Url
url = (f"{genesis_url}username={user_id}&password={password}&language=de&name={cubecode}&area={areatype}"
       f"&compress=true&contents={content}&startyear={start_year}")

# Add Classifyers to url
if classifier1:
       url += f'&classifyingvariable1={classifier1}'
if key1:
       url += f'&classifyingkey1={key1}'

# request
response = requests.get(url)
data = json.loads(response.text)["Object"]['Content'].split('\n')

# Compile a regex pattern to find sequences of digits ending with "=100"
info_pattern = re.compile(r'\d+=100')

# Extract only the parts of lines that match the pattern "*=100"
info_matches = []
for line in data:
    matches = info_pattern.findall(line)  # find all matches in a line
    info_matches.extend(matches)  # add found matches to the list

# Convert info_matches to a single string to append to each filtered line
info_matches_str = ', '.join(info_matches)

# Filter out the relevant lines and append the matches string to each
filtered_response = [line + " " + info_matches_str for line in data if 'D' in line and 'e' in line and ('MONAT' in line or 'QUART' in line)]

#rprint(filtered_response)
# Split each line into its components and extract the relevant information

data = [{'field_D': parts[0],
         'classifyingkey1': parts[1],
         'field_DG': parts[2],
         'period': parts[3],
         'year': int(parts[4]),
         'value': float(parts[5]),
         'field_e': parts[6],
         'base': info_matches_str
        }
        for parts in (line.split(';') for line in filtered_response)]

# Create a DataFrame from the extracted data
df = pd.DataFrame(data)

# Determine if the data is monthly or quarterly based on the unique values in the 'period' column
if df['period'].str.contains('Q').any():
    period_key = 'quarter'
else:
    period_key = 'month'

# Create result dict
result = {'cubeCode': cubecode, 'content': content, 'classifyingVar1': classifier1, 'classifyingKey1': key1, 'data': []}
for year, group in df.groupby('year'):
    year_data = {
        'year': year,
        'df': [{
            period_key: row['period'],
            'value': row['value'],
            'base': row['base']
            } for _, row in group.iterrows()]
    }
    result['data'].append(year_data)

j = json.dumps(result, indent=4)
rprint(j)

{
    "cubeCode": "61241BM006",
    "content": "",
    "classifyingVar1": "GP19M6",
    "classifyingKey1": "GP19-351113",
    "data": [
        {
            "year": 1976,
            "df": [
                {
                    "month": "MONAT01",
                    "value": 45.1,
                    "base": "2021=100"
                },
                {
                    "month": "MONAT02",
                    "value": 45.1,
                    "base": "2021=100"
                },
                {
                    "month": "MONAT03",
                    "value": 45.1,
                    "base": "2021=100"
                },
                {
                    "month": "MONAT04",
                    "value": 45.6,
                    "base": "2021=100"
                },
                {
                    "month": "MONAT05",
                    "value": 45.6,
                    "base": "2021=100"
                },
                {
                    "month": "MONAT06",
                    "value": 45.6,
                    "base": "2021=100"
                },
                {
                    "month": "MONAT07",
                    "value": 45.6,
                    "base": "2021=100"
                },
                {
                    "month": "MONAT08",
                    "value": 45.6,
                    "base": "2021=100"
                },
                {
                    "month": "MONAT09",
                    "value": 45.6,
                    "base": "2021=100"
                },
                {
                    "month": "MONAT10",
                    "value": 45.6,
                    "base": "2021=100"
                },
                {
                    "month": "MONAT11",
                    "value": 45.6,
                    "base": "2021=100"
                },
                {
                    "month": "MONAT12",
                    "value": 45.6,
                    "base": "2021=100"
                }
            ]
        },
        {
            "year": 1977,
            "df": [
                {
                    "month": "MONAT01",
                    "value": 45.6,
                    "base": "2021=100"
                },
                {
                    "month": "MONAT02",
                    "value": 45.6,
                    "base": "2021=100"
                },
                {
                    "month": "MONAT03",
                    "value": 45.6,
                    "base": "2021=100"
                },
                {
                    "month": "MONAT04",
                    "value": 45.6,
                    "base": "2021=100"
                },
                {
                    "month": "MONAT05",
                    "value": 45.6,
                    "base": "2021=100"
                },
                {
                    "month": "MONAT06",
                    "value": 45.6,
                    "base": "2021=100"
                },
                {
                    "month": "MONAT07",
                    "value": 45.7,
                    "base": "2021=100"
                },
                {
                    "month": "MONAT08",
                    "value": 45.7,
                    "base": "2021=100"
                },
                {
                    "month": "MONAT09",
                    "value": 45.7,
                    "base": "2021=100"
                },
                {
                    "month": "MONAT10",
                    "value": 45.8,
                    "base": "2021=100"
                },
                {
                    "month": "MONAT11",
                    "value": 45.8,
                    "base": "2021=100"
                },
                {
                    "month": "MONAT12",
                    "value": 45.8,
                    "base": "2021=100"
                }
            ]
        },
        {
            "year": 1978,
            "df": [
                {
      

In [22]:
# Index der Erzeugerpreise Investitionsgüter
cubecode = '61241BM008'
areatype = 'all'
content = ''
start_year = ''
classifier1 = 'GP19N2'
key1 = 'GP-X008'
lang = 'en'

# Destatis Base Url
url = (f"{genesis_url}username={user_id}&password={password}&language=de&name={cubecode}&area={areatype}"
       f"&compress=true&contents={content}&startyear={start_year}")

# Add Classifyers to url
if classifier1:
       url += f'&classifyingvariable1={classifier1}'
if key1:
       url += f'&classifyingkey1={key1}'

# request
response = requests.get(url)
data = json.loads(response.text)["Object"]['Content'].split('\n')

# Compile a regex pattern to find sequences of digits ending with "=100"
info_pattern = re.compile(r'\d+=100')

# Extract only the parts of lines that match the pattern "*=100"
info_matches = []
for line in data:
    matches = info_pattern.findall(line)  # find all matches in a line
    info_matches.extend(matches)  # add found matches to the list

# Convert info_matches to a single string to append to each filtered line
info_matches_str = ', '.join(info_matches)

# Filter out the relevant lines and append the matches string to each
filtered_response = [line + " " + info_matches_str for line in data if 'D' in line and 'e' in line and ('MONAT' in line or 'QUART' in line)]

#rprint(filtered_response)
# Split each line into its components and extract the relevant information

data = [{'field_D': parts[0],
         'classifyingkey1': parts[1],
         'field_DG': parts[2],
         'period': parts[3],
         'year': int(parts[4]),
         'value': float(parts[5]),
         'field_e': parts[6],
         'base': info_matches_str
        }
        for parts in (line.split(';') for line in filtered_response)]

# Create a DataFrame from the extracted data
df = pd.DataFrame(data)

# Determine if the data is monthly or quarterly based on the unique values in the 'period' column
if df['period'].str.contains('Q').any():
    period_key = 'quarter'
else:
    period_key = 'month'

# Create result dict
result = {'cubeCode': cubecode, 'content': content, 'classifyingVar1': classifier1, 'classifyingKey1': key1, 'data': []}
for year, group in df.groupby('year'):
    year_data = {
        'year': year,
        'df': [{
            period_key: row['period'],
            'value': row['value'],
            'base': row['base']
            } for _, row in group.iterrows()]
    }
    result['data'].append(year_data)

j = json.dumps(result, indent=4)
rprint(j)

{
    "cubeCode": "61241BM008",
    "content": "",
    "classifyingVar1": "GP19N2",
    "classifyingKey1": "GP-X008",
    "data": [
        {
            "year": 1976,
            "df": [
                {
                    "month": "MONAT01",
                    "value": 46.6,
                    "base": "2021=100"
                },
                {
                    "month": "MONAT02",
                    "value": 46.9,
                    "base": "2021=100"
                },
                {
                    "month": "MONAT03",
                    "value": 47.0,
                    "base": "2021=100"
                },
                {
                    "month": "MONAT04",
                    "value": 47.7,
                    "base": "2021=100"
                },
                {
                    "month": "MONAT05",
                    "value": 47.8,
                    "base": "2021=100"
                },
                {
                    "month": "MONAT06",
                    "value": 48.0,
                    "base": "2021=100"
                },
                {
                    "month": "MONAT07",
                    "value": 48.1,
                    "base": "2021=100"
                },
                {
                    "month": "MONAT08",
                    "value": 48.2,
                    "base": "2021=100"
                },
                {
                    "month": "MONAT09",
                    "value": 48.4,
                    "base": "2021=100"
                },
                {
                    "month": "MONAT10",
                    "value": 48.4,
                    "base": "2021=100"
                },
                {
                    "month": "MONAT11",
                    "value": 48.4,
                    "base": "2021=100"
                },
                {
                    "month": "MONAT12",
                    "value": 48.4,
                    "base": "2021=100"
                }
            ]
        },
        {
            "year": 1977,
            "df": [
                {
                    "month": "MONAT01",
                    "value": 48.8,
                    "base": "2021=100"
                },
                {
                    "month": "MONAT02",
                    "value": 49.1,
                    "base": "2021=100"
                },
                {
                    "month": "MONAT03",
                    "value": 49.4,
                    "base": "2021=100"
                },
                {
                    "month": "MONAT04",
                    "value": 49.8,
                    "base": "2021=100"
                },
                {
                    "month": "MONAT05",
                    "value": 50.0,
                    "base": "2021=100"
                },
                {
                    "month": "MONAT06",
                    "value": 50.0,
                    "base": "2021=100"
                },
                {
                    "month": "MONAT07",
                    "value": 50.1,
                    "base": "2021=100"
                },
                {
                    "month": "MONAT08",
                    "value": 50.1,
                    "base": "2021=100"
                },
                {
                    "month": "MONAT09",
                    "value": 50.1,
                    "base": "2021=100"
                },
                {
                    "month": "MONAT10",
                    "value": 50.1,
                    "base": "2021=100"
                },
                {
                    "month": "MONAT11",
                    "value": 50.1,
                    "base": "2021=100"
                },
                {
                    "month": "MONAT12",
                    "value": 50.1,
                    "base": "2021=100"
                }
            ]
        },
        {
            "year": 1978,
            "df": [
                {
          

In [23]:
# Lohnindex Energieversorgung
cubecode = '62221BV001'
areatype = 'all'
content = 'VST066'
start_year = ''
classifier1 = 'WZ08C7'
key1 = 'WZ08-D'
lang = 'en'

# Destatis Base Url
url = (f"{genesis_url}username={user_id}&password={password}&language=de&name={cubecode}&area={areatype}"
       f"&compress=true&contents={content}&startyear={start_year}")

# Add Classifyers to url
if classifier1:
       url += f'&classifyingvariable1={classifier1}'
if key1:
       url += f'&classifyingkey1={key1}'

# request
response = requests.get(url)
data = json.loads(response.text)["Object"]['Content'].split('\n')

# Compile a regex pattern to find sequences of digits ending with "=100"
info_pattern = re.compile(r'\d+=100')

# Extract only the parts of lines that match the pattern "*=100"
info_matches = []
for line in data:
    matches = info_pattern.findall(line)  # find all matches in a line
    info_matches.extend(matches)  # add found matches to the list

# Convert info_matches to a single string to append to each filtered line
info_matches_str = ', '.join(info_matches)

# Filter out the relevant lines and append the matches string to each
filtered_response = [line + " " + info_matches_str for line in data if 'D' in line and 'e' in line and ('MONAT' in line or 'QUART' in line)]

#rprint(filtered_response)
# Split each line into its components and extract the relevant information

data = [{'field_D': parts[0],
         'classifyingkey1': parts[1],
         'field_DG': parts[2],
         'period': parts[3],
         'year': int(parts[4]),
         'value': float(parts[5]),
         'field_e': parts[6],
         'base': info_matches_str
        }
        for parts in (line.split(';') for line in filtered_response)]

# Create a DataFrame from the extracted data
df = pd.DataFrame(data)

# Determine if the data is monthly or quarterly based on the unique values in the 'period' column
if df['period'].str.contains('Q').any():
    period_key = 'quarter'
else:
    period_key = 'month'

# Create result dict
result = {'cubeCode': cubecode, 'content': content, 'classifyingVar1': classifier1, 'classifyingKey1': key1, 'data': []}
for year, group in df.groupby('year'):
    year_data = {
        'year': year,
        'df': [{
            period_key: row['period'],
            'value': row['value'],
            'base': row['base']
            } for _, row in group.iterrows()]
    }
    result['data'].append(year_data)

j = json.dumps(result, indent=4)
rprint(j)

{
    "cubeCode": "62221BV001",
    "content": "VST066",
    "classifyingVar1": "WZ08C7",
    "classifyingKey1": "WZ08-D",
    "data": [
        {
            "year": 1995,
            "df": [
                {
                    "quarter": "QUART1",
                    "value": 56.8,
                    "base": "2020=100"
                },
                {
                    "quarter": "QUART2",
                    "value": 57.3,
                    "base": "2020=100"
                },
                {
                    "quarter": "QUART3",
                    "value": 59.0,
                    "base": "2020=100"
                },
                {
                    "quarter": "QUART4",
                    "value": 59.0,
                    "base": "2020=100"
                }
            ]
        },
        {
            "year": 1996,
            "df": [
                {
                    "quarter": "QUART1",
                    "value": 59.0,
                    "base": "2020=100"
                },
                {
                    "quarter": "QUART2",
                    "value": 59.5,
                    "base": "2020=100"
                },
                {
                    "quarter": "QUART3",
                    "value": 59.7,
                    "base": "2020=100"
                },
                {
                    "quarter": "QUART4",
                    "value": 59.9,
                    "base": "2020=100"
                }
            ]
        },
        {
            "year": 1997,
            "df": [
                {
                    "quarter": "QUART1",
                    "value": 60.3,
                    "base": "2020=100"
                },
                {
                    "quarter": "QUART2",
                    "value": 60.5,
                    "base": "2020=100"
                },
                {
                    "quarter": "QUART3",
                    "value": 60.6,
                    "base": "2020=100"
                },
                {
                    "quarter": "QUART4",
                    "value": 60.8,
                    "base": "2020=100"
                }
            ]
        },
        {
            "year": 1998,
            "df": [
                {
                    "quarter": "QUART1",
                    "value": 61.4,
                    "base": "2020=100"
                },
                {
                    "quarter": "QUART2",
                    "value": 61.4,
                    "base": "2020=100"
                },
                {
                    "quarter": "QUART3",
                    "value": 61.6,
                    "base": "2020=100"
                },
                {
                    "quarter": "QUART4",
                    "value": 61.7,
                    "base": "2020=100"
                }
            ]
        },
        {
            "year": 1999,
            "df": [
                {
                    "quarter": "QUART1",
                    "value": 61.9,
                    "base": "2020=100"
                },
                {
                    "quarter": "QUART2",
                    "value": 62.8,
                    "base": "2020=100"
                },
                {
                    "quarter": "QUART3",
                    "value": 63.5,
                    "base": "2020=100"
                },
                {
                    "quarter": "QUART4",
                    "value": 63.5,
                    "base": "2020=100"
                }
            ]
        },
        {
            "year": 2000,
            "df": [
                {
                    "quarter": "QUART1",
                    "value": 63.7,
                    "base": "2020=100"
                },
                {
                    "quarter": "QUART2",
                    "value": 63.7,
                    "base": "2020=100"
                },
                {
                    "quarter": "QUART3",
    

In [24]:
# Lohnindex Energie- u. Wasserversorgung
cubecode = '62221BV001'
areatype = 'all'
content = 'VST066'
start_year = ''
classifier1 = 'WZ08C7'
key1 = 'WZ08-D-06'
lang = 'en'

# Destatis Base Url
url = (f"{genesis_url}username={user_id}&password={password}&language=de&name={cubecode}&area={areatype}"
       f"&compress=true&contents={content}&startyear={start_year}")

# Add Classifyers to url
if classifier1:
       url += f'&classifyingvariable1={classifier1}'
if key1:
       url += f'&classifyingkey1={key1}'

# request
response = requests.get(url)
data = json.loads(response.text)["Object"]['Content'].split('\n')

# Compile a regex pattern to find sequences of digits ending with "=100"
info_pattern = re.compile(r'\d+=100')

# Extract only the parts of lines that match the pattern "*=100"
info_matches = []
for line in data:
    matches = info_pattern.findall(line)  # find all matches in a line
    info_matches.extend(matches)  # add found matches to the list

# Convert info_matches to a single string to append to each filtered line
info_matches_str = ', '.join(info_matches)

# Filter out the relevant lines and append the matches string to each
filtered_response = [line + " " + info_matches_str for line in data if 'D' in line and 'e' in line and ('MONAT' in line or 'QUART' in line)]

#rprint(filtered_response)
# Split each line into its components and extract the relevant information

data = [{'field_D': parts[0],
         'classifyingkey1': parts[1],
         'field_DG': parts[2],
         'period': parts[3],
         'year': int(parts[4]),
         'value': float(parts[5]),
         'field_e': parts[6],
         'base': info_matches_str
        }
        for parts in (line.split(';') for line in filtered_response)]

# Create a DataFrame from the extracted data
df = pd.DataFrame(data)

# Determine if the data is monthly or quarterly based on the unique values in the 'period' column
if df['period'].str.contains('Q').any():
    period_key = 'quarter'
else:
    period_key = 'month'

# Create result dict
result = {'cubeCode': cubecode, 'content': content, 'classifyingVar1': classifier1, 'classifyingKey1': key1, 'data': []}
for year, group in df.groupby('year'):
    year_data = {
        'year': year,
        'df': [{
            period_key: row['period'],
            'value': row['value'],
            'base': row['base']
            } for _, row in group.iterrows()]
    }
    result['data'].append(year_data)

j = json.dumps(result, indent=4)
rprint(j)

{
    "cubeCode": "62221BV001",
    "content": "VST066",
    "classifyingVar1": "WZ08C7",
    "classifyingKey1": "WZ08-D-06",
    "data": [
        {
            "year": 1995,
            "df": [
                {
                    "quarter": "QUART1",
                    "value": 56.6,
                    "base": "2020=100"
                },
                {
                    "quarter": "QUART2",
                    "value": 57.0,
                    "base": "2020=100"
                },
                {
                    "quarter": "QUART3",
                    "value": 58.7,
                    "base": "2020=100"
                },
                {
                    "quarter": "QUART4",
                    "value": 58.8,
                    "base": "2020=100"
                }
            ]
        },
        {
            "year": 1996,
            "df": [
                {
                    "quarter": "QUART1",
                    "value": 58.8,
                    "base": "2020=100"
                },
                {
                    "quarter": "QUART2",
                    "value": 59.2,
                    "base": "2020=100"
                },
                {
                    "quarter": "QUART3",
                    "value": 59.5,
                    "base": "2020=100"
                },
                {
                    "quarter": "QUART4",
                    "value": 59.6,
                    "base": "2020=100"
                }
            ]
        },
        {
            "year": 1997,
            "df": [
                {
                    "quarter": "QUART1",
                    "value": 60.1,
                    "base": "2020=100"
                },
                {
                    "quarter": "QUART2",
                    "value": 60.2,
                    "base": "2020=100"
                },
                {
                    "quarter": "QUART3",
                    "value": 60.4,
                    "base": "2020=100"
                },
                {
                    "quarter": "QUART4",
                    "value": 60.5,
                    "base": "2020=100"
                }
            ]
        },
        {
            "year": 1998,
            "df": [
                {
                    "quarter": "QUART1",
                    "value": 61.2,
                    "base": "2020=100"
                },
                {
                    "quarter": "QUART2",
                    "value": 61.2,
                    "base": "2020=100"
                },
                {
                    "quarter": "QUART3",
                    "value": 61.4,
                    "base": "2020=100"
                },
                {
                    "quarter": "QUART4",
                    "value": 61.4,
                    "base": "2020=100"
                }
            ]
        },
        {
            "year": 1999,
            "df": [
                {
                    "quarter": "QUART1",
                    "value": 61.6,
                    "base": "2020=100"
                },
                {
                    "quarter": "QUART2",
                    "value": 62.6,
                    "base": "2020=100"
                },
                {
                    "quarter": "QUART3",
                    "value": 63.3,
                    "base": "2020=100"
                },
                {
                    "quarter": "QUART4",
                    "value": 63.3,
                    "base": "2020=100"
                }
            ]
        },
        {
            "year": 2000,
            "df": [
                {
                    "quarter": "QUART1",
                    "value": 63.4,
                    "base": "2020=100"
                },
                {
                    "quarter": "QUART2",
                    "value": 63.4,
                    "base": "2020=100"
                },
                {
                    "quarter": "QUART3",
 

In [25]:
# Verbraucherpreisindex für Deutschland
cubecode = '61111BM001'
areatype = 'all'
content = ''
start_year = ''
classifier1 = ''
key1 = ''
lang = 'de'

# Destatis Base Url
url = (f"{genesis_url}username={user_id}&password={password}&language={lang}&area={areatype}&name={cubecode}")

if start_year:
       url += f'&startyear={start_year}'

if content:
       url += f'&contents={content}'
# Add Classifyers to url
if classifier1:
       url += f'&classifyingvariable1={classifier1}'
if key1:
       url += f'&classifyingkey1={key1}'

# request
response = requests.get(url)
data = json.loads(response.text)["Object"]['Content'].split('\n')

# Compile a regex pattern to find sequences of digits ending with "=100"
info_pattern = re.compile(r'\d+=100')

# Extract only the parts of lines that match the pattern "*=100"
info_matches = []
for line in data:
    matches = info_pattern.findall(line)  # find all matches in a line
    info_matches.extend(matches)  # add found matches to the list

# Convert info_matches to a single string to append to each filtered line
info_matches_str = ', '.join(info_matches)

# Filter out the relevant lines and append the matches string to each
filtered_response = [line + " " + info_matches_str for line in data if 'D' in line and 'e' in line and ('MONAT' in line or 'QUART' in line)]

# Split each line into its components and extract the relevant information

data = [{'field_D': parts[0],
         'field_DG': parts[1],
         'period': parts[2],
         'year': int(parts[3]),
         'value': float(parts[4]),
         'field_e': parts[5],
         'base': info_matches_str
        }
        for parts in (line.split(';') for line in filtered_response)]

# Create a DataFrame from the extracted data
df = pd.DataFrame(data)

# Determine if the data is monthly or quarterly based on the unique values in the 'period' column
if df['period'].str.contains('Q').any():
    period_key = 'quarter'
else:
    period_key = 'month'

# Create result dict
result = {'cubeCode': cubecode, 'content': content, 'classifyingVar1': classifier1, 'classifyingKey1': key1, 'data': []}
for year, group in df.groupby('year'):
    year_data = {
        'year': year,
        'df': [{
            period_key: row['period'],
            'value': row['value'],
            'base': row['base']
            } for _, row in group.iterrows()]
    }
    result['data'].append(year_data)

j = json.dumps(result, indent=4)
rprint(j)

{
    "cubeCode": "61111BM001",
    "content": "",
    "classifyingVar1": "",
    "classifyingKey1": "",
    "data": [
        {
            "year": 1991,
            "df": [
                {
                    "month": "MONAT01",
                    "value": 60.5,
                    "base": "2020=100"
                },
                {
                    "month": "MONAT02",
                    "value": 60.8,
                    "base": "2020=100"
                },
                {
                    "month": "MONAT03",
                    "value": 60.8,
                    "base": "2020=100"
                },
                {
                    "month": "MONAT04",
                    "value": 61.0,
                    "base": "2020=100"
                },
                {
                    "month": "MONAT05",
                    "value": 61.1,
                    "base": "2020=100"
                },
                {
                    "month": "MONAT06",
                    "value": 61.5,
                    "base": "2020=100"
                },
                {
                    "month": "MONAT07",
                    "value": 62.2,
                    "base": "2020=100"
                },
                {
                    "month": "MONAT08",
                    "value": 62.2,
                    "base": "2020=100"
                },
                {
                    "month": "MONAT09",
                    "value": 62.2,
                    "base": "2020=100"
                },
                {
                    "month": "MONAT10",
                    "value": 63.2,
                    "base": "2020=100"
                },
                {
                    "month": "MONAT11",
                    "value": 63.4,
                    "base": "2020=100"
                },
                {
                    "month": "MONAT12",
                    "value": 63.5,
                    "base": "2020=100"
                }
            ]
        },
        {
            "year": 1992,
            "df": [
                {
                    "month": "MONAT01",
                    "value": 63.9,
                    "base": "2020=100"
                },
                {
                    "month": "MONAT02",
                    "value": 64.3,
                    "base": "2020=100"
                },
                {
                    "month": "MONAT03",
                    "value": 64.5,
                    "base": "2020=100"
                },
                {
                    "month": "MONAT04",
                    "value": 64.7,
                    "base": "2020=100"
                },
                {
                    "month": "MONAT05",
                    "value": 64.9,
                    "base": "2020=100"
                },
                {
                    "month": "MONAT06",
                    "value": 65.1,
                    "base": "2020=100"
                },
                {
                    "month": "MONAT07",
                    "value": 65.3,
                    "base": "2020=100"
                },
                {
                    "month": "MONAT08",
                    "value": 65.3,
                    "base": "2020=100"
                },
                {
                    "month": "MONAT09",
                    "value": 65.3,
                    "base": "2020=100"
                },
                {
                    "month": "MONAT10",
                    "value": 65.3,
                    "base": "2020=100"
                },
                {
                    "month": "MONAT11",
                    "value": 65.6,
                    "base": "2020=100"
                },
                {
                    "month": "MONAT12",
                    "value": 65.7,
                    "base": "2020=100"
                }
            ]
        },
        {
            "year": 1993,
            "df": [
                {
                    "mo

In [26]:
# Fernwärmeindex
cubecode = '61241BM007'
areatype = 'all'
content = ''
start_year = ''
classifier1 = 'GP19N1'
key1 = 'GP19-353010031'
lang = 'de'

# Destatis Base Url
url = (f"{genesis_url}username={user_id}&password={password}&language={lang}&area={areatype}&name={cubecode}")

if start_year:
       url += f'&startyear={start_year}'

if content:
       url += f'&contents={content}'
# Add Classifyers to url
if classifier1:
       url += f'&classifyingvariable1={classifier1}'
if key1:
       url += f'&classifyingkey1={key1}'

# request
response = requests.get(url)
data = json.loads(response.text)["Object"]['Content'].split('\n')

# Compile a regex pattern to find sequences of digits ending with "=100"
info_pattern = re.compile(r'\d+=100')

# Extract only the parts of lines that match the pattern "*=100"
info_matches = []
for line in data:
    matches = info_pattern.findall(line)  # find all matches in a line
    info_matches.extend(matches)  # add found matches to the list

# Convert info_matches to a single string to append to each filtered line
info_matches_str = ', '.join(info_matches)

# Filter out the relevant lines and append the matches string to each
filtered_response = [line + " " + info_matches_str for line in data if 'D' in line and 'e' in line and ('MONAT' in line or 'QUART' in line)]

#rprint(filtered_response)
# Split each line into its components and extract the relevant information

data = [{'field_D': parts[0],
         'classifyingkey1': parts[1],
         'field_DG': parts[2],
         'period': parts[3],
         'year': int(parts[4]),
         'value': float(parts[5]),
         'field_e': parts[6],
         'base': info_matches_str
        }
        for parts in (line.split(';') for line in filtered_response)]

# Create a DataFrame from the extracted data
df = pd.DataFrame(data)

# Determine if the data is monthly or quarterly based on the unique values in the 'period' column
if df['period'].str.contains('Q').any():
    period_key = 'quarter'
else:
    period_key = 'month'

# Create result dict
result = {'cubeCode': cubecode, 'content': content, 'classifyingVar1': classifier1, 'classifyingKey1': key1, 'data': []}
for year, group in df.groupby('year'):
    year_data = {
        'year': year,
        'df': [{
            period_key: row['period'],
            'value': row['value'],
            'base': row['base']
            } for _, row in group.iterrows()]
    }
    result['data'].append(year_data)

j = json.dumps(result, indent=4)
rprint(j)

{
    "cubeCode": "61241BM007",
    "content": "",
    "classifyingVar1": "GP19N1",
    "classifyingKey1": "GP19-353010031",
    "data": [
        {
            "year": 2000,
            "df": [
                {
                    "month": "MONAT01",
                    "value": 55.7,
                    "base": "2021=100"
                },
                {
                    "month": "MONAT02",
                    "value": 55.8,
                    "base": "2021=100"
                },
                {
                    "month": "MONAT03",
                    "value": 55.7,
                    "base": "2021=100"
                },
                {
                    "month": "MONAT04",
                    "value": 56.2,
                    "base": "2021=100"
                },
                {
                    "month": "MONAT05",
                    "value": 56.4,
                    "base": "2021=100"
                },
                {
                    "month": "MONAT06",
                    "value": 56.4,
                    "base": "2021=100"
                },
                {
                    "month": "MONAT07",
                    "value": 56.9,
                    "base": "2021=100"
                },
                {
                    "month": "MONAT08",
                    "value": 57.2,
                    "base": "2021=100"
                },
                {
                    "month": "MONAT09",
                    "value": 57.7,
                    "base": "2021=100"
                },
                {
                    "month": "MONAT10",
                    "value": 58.7,
                    "base": "2021=100"
                },
                {
                    "month": "MONAT11",
                    "value": 59.1,
                    "base": "2021=100"
                },
                {
                    "month": "MONAT12",
                    "value": 59.1,
                    "base": "2021=100"
                }
            ]
        },
        {
            "year": 2001,
            "df": [
                {
                    "month": "MONAT01",
                    "value": 61.5,
                    "base": "2021=100"
                },
                {
                    "month": "MONAT02",
                    "value": 62.1,
                    "base": "2021=100"
                },
                {
                    "month": "MONAT03",
                    "value": 62.0,
                    "base": "2021=100"
                },
                {
                    "month": "MONAT04",
                    "value": 62.6,
                    "base": "2021=100"
                },
                {
                    "month": "MONAT05",
                    "value": 63.0,
                    "base": "2021=100"
                },
                {
                    "month": "MONAT06",
                    "value": 63.2,
                    "base": "2021=100"
                },
                {
                    "month": "MONAT07",
                    "value": 63.2,
                    "base": "2021=100"
                },
                {
                    "month": "MONAT08",
                    "value": 63.7,
                    "base": "2021=100"
                },
                {
                    "month": "MONAT09",
                    "value": 63.8,
                    "base": "2021=100"
                },
                {
                    "month": "MONAT10",
                    "value": 63.7,
                    "base": "2021=100"
                },
                {
                    "month": "MONAT11",
                    "value": 63.8,
                    "base": "2021=100"
                },
                {
                    "month": "MONAT12",
                    "value": 63.8,
                    "base": "2021=100"
                }
            ]
        },
        {
            "year": 2002,
            "df": [
                {
   

In [27]:
# Erdgas, bei Abgabe an Handel und Gewerbe
cubecode = '61241BM007'
areatype = 'all'
content = ''
start_year = ''
classifier1 = 'GP19N1'
key1 = 'GP19-352222200'
lang = 'de'

# Destatis Base Url
url = (f"{genesis_url}username={user_id}&password={password}&language={lang}&area={areatype}&name={cubecode}")

if start_year:
       url += f'&startyear={start_year}'

if content:
       url += f'&contents={content}'
# Add Classifyers to url
if classifier1:
       url += f'&classifyingvariable1={classifier1}'
if key1:
       url += f'&classifyingkey1={key1}'

# request
response = requests.get(url)
data = json.loads(response.text)["Object"]['Content'].split('\n')

# Compile a regex pattern to find sequences of digits ending with "=100"
info_pattern = re.compile(r'\d+=100')

# Extract only the parts of lines that match the pattern "*=100"
info_matches = []
for line in data:
    matches = info_pattern.findall(line)  # find all matches in a line
    info_matches.extend(matches)  # add found matches to the list

# Convert info_matches to a single string to append to each filtered line
info_matches_str = ', '.join(info_matches)

# Filter out the relevant lines and append the matches string to each
filtered_response = [line + " " + info_matches_str for line in data if 'D' in line and 'e' in line and ('MONAT' in line or 'QUART' in line)]

#rprint(filtered_response)
# Split each line into its components and extract the relevant information

data = [{'field_D': parts[0],
         'classifyingkey1': parts[1],
         'field_DG': parts[2],
         'period': parts[3],
         'year': int(parts[4]),
         'value': float(parts[5]),
         'field_e': parts[6],
         'base': info_matches_str
        }
        for parts in (line.split(';') for line in filtered_response)]

# Create a DataFrame from the extracted data
df = pd.DataFrame(data)

# Determine if the data is monthly or quarterly based on the unique values in the 'period' column
if df['period'].str.contains('Q').any():
    period_key = 'quarter'
else:
    period_key = 'month'

# Create result dict
result = {'cubeCode': cubecode, 'content': content, 'classifyingVar1': classifier1, 'classifyingKey1': key1, 'data': []}
for year, group in df.groupby('year'):
    year_data = {
        'year': year,
        'df': [{
            period_key: row['period'],
            'value': row['value'],
            'base': row['base']
            } for _, row in group.iterrows()]
    }
    result['data'].append(year_data)

j = json.dumps(result, indent=4)
rprint(j)

{
    "cubeCode": "61241BM007",
    "content": "",
    "classifyingVar1": "GP19N1",
    "classifyingKey1": "GP19-352222200",
    "data": [
        {
            "year": 2000,
            "df": [
                {
                    "month": "MONAT01",
                    "value": 46.3,
                    "base": "2021=100"
                },
                {
                    "month": "MONAT02",
                    "value": 46.5,
                    "base": "2021=100"
                },
                {
                    "month": "MONAT03",
                    "value": 46.5,
                    "base": "2021=100"
                },
                {
                    "month": "MONAT04",
                    "value": 50.0,
                    "base": "2021=100"
                },
                {
                    "month": "MONAT05",
                    "value": 50.9,
                    "base": "2021=100"
                },
                {
                    "month": "MONAT06",
                    "value": 51.6,
                    "base": "2021=100"
                },
                {
                    "month": "MONAT07",
                    "value": 53.2,
                    "base": "2021=100"
                },
                {
                    "month": "MONAT08",
                    "value": 54.6,
                    "base": "2021=100"
                },
                {
                    "month": "MONAT09",
                    "value": 54.7,
                    "base": "2021=100"
                },
                {
                    "month": "MONAT10",
                    "value": 58.2,
                    "base": "2021=100"
                },
                {
                    "month": "MONAT11",
                    "value": 59.6,
                    "base": "2021=100"
                },
                {
                    "month": "MONAT12",
                    "value": 60.4,
                    "base": "2021=100"
                }
            ]
        },
        {
            "year": 2001,
            "df": [
                {
                    "month": "MONAT01",
                    "value": 65.5,
                    "base": "2021=100"
                },
                {
                    "month": "MONAT02",
                    "value": 66.5,
                    "base": "2021=100"
                },
                {
                    "month": "MONAT03",
                    "value": 66.5,
                    "base": "2021=100"
                },
                {
                    "month": "MONAT04",
                    "value": 67.7,
                    "base": "2021=100"
                },
                {
                    "month": "MONAT05",
                    "value": 67.2,
                    "base": "2021=100"
                },
                {
                    "month": "MONAT06",
                    "value": 67.2,
                    "base": "2021=100"
                },
                {
                    "month": "MONAT07",
                    "value": 66.8,
                    "base": "2021=100"
                },
                {
                    "month": "MONAT08",
                    "value": 66.6,
                    "base": "2021=100"
                },
                {
                    "month": "MONAT09",
                    "value": 66.6,
                    "base": "2021=100"
                },
                {
                    "month": "MONAT10",
                    "value": 63.7,
                    "base": "2021=100"
                },
                {
                    "month": "MONAT11",
                    "value": 63.4,
                    "base": "2021=100"
                },
                {
                    "month": "MONAT12",
                    "value": 63.4,
                    "base": "2021=100"
                }
            ]
        },
        {
            "year": 2002,
            "df": [
                {
   

In [28]:
# Holz i.Form v.Plättchen o.Schnitzeln aus Nadelholz
cubecode = '61241BM007'
areatype = 'all'
content = ''
start_year = ''
classifier1 = 'GP19N1'
key1 = 'GP19-161025030'
lang = 'de'

# Destatis Base Url
url = (f"{genesis_url}username={user_id}&password={password}&language={lang}&area={areatype}&name={cubecode}")

if start_year:
       url += f'&startyear={start_year}'

if content:
       url += f'&contents={content}'
# Add Classifyers to url
if classifier1:
       url += f'&classifyingvariable1={classifier1}'
if key1:
       url += f'&classifyingkey1={key1}'

# request
response = requests.get(url)
data = json.loads(response.text)["Object"]['Content'].split('\n')

# Compile a regex pattern to find sequences of digits ending with "=100"
info_pattern = re.compile(r'\d+=100')

# Extract only the parts of lines that match the pattern "*=100"
info_matches = []
for line in data:
    matches = info_pattern.findall(line)  # find all matches in a line
    info_matches.extend(matches)  # add found matches to the list

# Convert info_matches to a single string to append to each filtered line
info_matches_str = ', '.join(info_matches)

# Filter out the relevant lines and append the matches string to each
filtered_response = [line + " " + info_matches_str for line in data if 'D' in line and 'e' in line and ('MONAT' in line or 'QUART' in line)]

#rprint(filtered_response)
# Split each line into its components and extract the relevant information

data = [{'field_D': parts[0],
         'classifyingkey1': parts[1],
         'field_DG': parts[2],
         'period': parts[3],
         'year': int(parts[4]),
         'value': float(parts[5]),
         'field_e': parts[6],
         'base': info_matches_str
        }
        for parts in (line.split(';') for line in filtered_response)]

# Create a DataFrame from the extracted data
df = pd.DataFrame(data)

# Determine if the data is monthly or quarterly based on the unique values in the 'period' column
if df['period'].str.contains('Q').any():
    period_key = 'quarter'
else:
    period_key = 'month'

# Create result dict
result = {'cubeCode': cubecode, 'content': content, 'classifyingVar1': classifier1, 'classifyingKey1': key1, 'data': []}
for year, group in df.groupby('year'):
    year_data = {
        'year': year,
        'df': [{
            period_key: row['period'],
            'value': row['value'],
            'base': row['base']
            } for _, row in group.iterrows()]
    }
    result['data'].append(year_data)

j = json.dumps(result, indent=4)
rprint(j)

{
    "cubeCode": "61241BM007",
    "content": "",
    "classifyingVar1": "GP19N1",
    "classifyingKey1": "GP19-161025030",
    "data": [
        {
            "year": 2000,
            "df": [
                {
                    "month": "MONAT01",
                    "value": 95.9,
                    "base": "2021=100"
                },
                {
                    "month": "MONAT02",
                    "value": 96.8,
                    "base": "2021=100"
                },
                {
                    "month": "MONAT03",
                    "value": 92.9,
                    "base": "2021=100"
                },
                {
                    "month": "MONAT04",
                    "value": 91.5,
                    "base": "2021=100"
                },
                {
                    "month": "MONAT05",
                    "value": 91.2,
                    "base": "2021=100"
                },
                {
                    "month": "MONAT06",
                    "value": 91.2,
                    "base": "2021=100"
                },
                {
                    "month": "MONAT07",
                    "value": 88.0,
                    "base": "2021=100"
                },
                {
                    "month": "MONAT08",
                    "value": 87.8,
                    "base": "2021=100"
                },
                {
                    "month": "MONAT09",
                    "value": 88.3,
                    "base": "2021=100"
                },
                {
                    "month": "MONAT10",
                    "value": 87.2,
                    "base": "2021=100"
                },
                {
                    "month": "MONAT11",
                    "value": 87.2,
                    "base": "2021=100"
                },
                {
                    "month": "MONAT12",
                    "value": 87.5,
                    "base": "2021=100"
                }
            ]
        },
        {
            "year": 2001,
            "df": [
                {
                    "month": "MONAT01",
                    "value": 89.5,
                    "base": "2021=100"
                },
                {
                    "month": "MONAT02",
                    "value": 93.4,
                    "base": "2021=100"
                },
                {
                    "month": "MONAT03",
                    "value": 93.1,
                    "base": "2021=100"
                },
                {
                    "month": "MONAT04",
                    "value": 94.8,
                    "base": "2021=100"
                },
                {
                    "month": "MONAT05",
                    "value": 94.9,
                    "base": "2021=100"
                },
                {
                    "month": "MONAT06",
                    "value": 92.8,
                    "base": "2021=100"
                },
                {
                    "month": "MONAT07",
                    "value": 88.7,
                    "base": "2021=100"
                },
                {
                    "month": "MONAT08",
                    "value": 88.3,
                    "base": "2021=100"
                },
                {
                    "month": "MONAT09",
                    "value": 87.2,
                    "base": "2021=100"
                },
                {
                    "month": "MONAT10",
                    "value": 81.9,
                    "base": "2021=100"
                },
                {
                    "month": "MONAT11",
                    "value": 81.9,
                    "base": "2021=100"
                },
                {
                    "month": "MONAT12",
                    "value": 82.1,
                    "base": "2021=100"
                }
            ]
        },
        {
            "year": 2002,
            "df": [
                {
   

In [29]:
# Heizöl, leicht, Abgabe an Verbraucher
cubecode = '61241BM007'
areatype = 'all'
content = ''
start_year = ''
classifier1 = 'GP19N1'
key1 = 'GP19-1920260072'
lang = 'de'

# Destatis Base Url
url = (f"{genesis_url}username={user_id}&password={password}&language={lang}&area={areatype}&name={cubecode}")

if start_year:
       url += f'&startyear={start_year}'

if content:
       url += f'&contents={content}'
# Add Classifyers to url
if classifier1:
       url += f'&classifyingvariable1={classifier1}'
if key1:
       url += f'&classifyingkey1={key1}'

# request
response = requests.get(url)
data = json.loads(response.text)["Object"]['Content'].split('\n')

# Compile a regex pattern to find sequences of digits ending with "=100"
info_pattern = re.compile(r'\d+=100')

# Extract only the parts of lines that match the pattern "*=100"
info_matches = []
for line in data:
    matches = info_pattern.findall(line)  # find all matches in a line
    info_matches.extend(matches)  # add found matches to the list

# Convert info_matches to a single string to append to each filtered line
info_matches_str = ', '.join(info_matches)

# Filter out the relevant lines and append the matches string to each
filtered_response = [line + " " + info_matches_str for line in data if 'D' in line and 'e' in line and ('MONAT' in line or 'QUART' in line)]

#rprint(filtered_response)
# Split each line into its components and extract the relevant information

data = [{'field_D': parts[0],
         'classifyingkey1': parts[1],
         'field_DG': parts[2],
         'period': parts[3],
         'year': int(parts[4]),
         'value': float(parts[5]),
         'field_e': parts[6],
         'base': info_matches_str
        }
        for parts in (line.split(';') for line in filtered_response)]

# Create a DataFrame from the extracted data
df = pd.DataFrame(data)

# Determine if the data is monthly or quarterly based on the unique values in the 'period' column
if df['period'].str.contains('Q').any():
    period_key = 'quarter'
else:
    period_key = 'month'

# Create result dict
result = {'cubeCode': cubecode, 'content': content, 'classifyingVar1': classifier1, 'classifyingKey1': key1, 'data': []}
for year, group in df.groupby('year'):
    year_data = {
        'year': year,
        'df': [{
            period_key: row['period'],
            'value': row['value'],
            'base': row['base']
            } for _, row in group.iterrows()]
    }
    result['data'].append(year_data)

j = json.dumps(result, indent=4)
rprint(j)

{
    "cubeCode": "61241BM007",
    "content": "",
    "classifyingVar1": "GP19N1",
    "classifyingKey1": "GP19-1920260072",
    "data": [
        {
            "year": 1976,
            "df": [
                {
                    "month": "MONAT01",
                    "value": 22.8,
                    "base": "2021=100"
                },
                {
                    "month": "MONAT02",
                    "value": 23.5,
                    "base": "2021=100"
                },
                {
                    "month": "MONAT03",
                    "value": 23.2,
                    "base": "2021=100"
                },
                {
                    "month": "MONAT04",
                    "value": 23.6,
                    "base": "2021=100"
                },
                {
                    "month": "MONAT05",
                    "value": 23.0,
                    "base": "2021=100"
                },
                {
                    "month": "MONAT06",
                    "value": 23.6,
                    "base": "2021=100"
                },
                {
                    "month": "MONAT07",
                    "value": 23.6,
                    "base": "2021=100"
                },
                {
                    "month": "MONAT08",
                    "value": 24.0,
                    "base": "2021=100"
                },
                {
                    "month": "MONAT09",
                    "value": 24.1,
                    "base": "2021=100"
                },
                {
                    "month": "MONAT10",
                    "value": 23.5,
                    "base": "2021=100"
                },
                {
                    "month": "MONAT11",
                    "value": 22.1,
                    "base": "2021=100"
                },
                {
                    "month": "MONAT12",
                    "value": 23.5,
                    "base": "2021=100"
                }
            ]
        },
        {
            "year": 1977,
            "df": [
                {
                    "month": "MONAT01",
                    "value": 23.6,
                    "base": "2021=100"
                },
                {
                    "month": "MONAT02",
                    "value": 24.2,
                    "base": "2021=100"
                },
                {
                    "month": "MONAT03",
                    "value": 23.2,
                    "base": "2021=100"
                },
                {
                    "month": "MONAT04",
                    "value": 24.0,
                    "base": "2021=100"
                },
                {
                    "month": "MONAT05",
                    "value": 23.5,
                    "base": "2021=100"
                },
                {
                    "month": "MONAT06",
                    "value": 23.5,
                    "base": "2021=100"
                },
                {
                    "month": "MONAT07",
                    "value": 23.2,
                    "base": "2021=100"
                },
                {
                    "month": "MONAT08",
                    "value": 23.0,
                    "base": "2021=100"
                },
                {
                    "month": "MONAT09",
                    "value": 22.8,
                    "base": "2021=100"
                },
                {
                    "month": "MONAT10",
                    "value": 23.4,
                    "base": "2021=100"
                },
                {
                    "month": "MONAT11",
                    "value": 23.4,
                    "base": "2021=100"
                },
                {
                    "month": "MONAT12",
                    "value": 23.5,
                    "base": "2021=100"
                }
            ]
        },
        {
            "year": 1978,
            "df": [
                {
  